In [ ]:
import ipywidgets as widgets
import geoarrow.pyarrow as ga
import pyarrow as pa
import pyarrow.compute as pc
import pyarrow.dataset as ds
from h3ronpy.vector import  cells_to_coordinates
from IPython.display import display
from lonboard import Map, H3HexagonLayer, ScatterplotLayer
from lonboard.colormap import apply_continuous_cmap
from palettable.scientific.diverging import Roma_10

In [ ]:
# load data set
tbl = ds.dataset("data/lonboard_h3_repro.parquet").to_table()

# convert h3_index to coordinates for comparison between H3HexagonLayer and ScatterplotLayer

coords = cells_to_coordinates(tbl.column("h3_index"))
point_struct_arr = pa.StructArray.from_arrays(
    [coords.column("lng"), coords.column("lat")],
    names=["x", "y"],
)

# Wrap with the geoarrow point type
point_arr = (
    ga.point()
    .with_dimensions("xy")
    .with_crs("EPSG:4326")
    .wrap_array(point_struct_arr)
)

tbl = tbl.append_column("geometry", point_arr)

In [ ]:
# Split data into binned tables for each frame
time_bins = tbl.column("time_bin")
unique_bins = pc.unique(time_bins).to_pylist()
unique_bins.sort()

print(f"Found {len(unique_bins)} unique bins in the data")
print(f"Time range: {unique_bins[0]} to {unique_bins[-1]}")

bin_tables = {}
for bin in unique_bins:
    mask = pc.equal(time_bins, bin)
    layer_tbl = tbl.filter(mask)
    bin_tables[bin] = layer_tbl
    print(f"Minute {bin}: {len(layer_tbl)} rows")

In [ ]:
# Concatenate and compute global statistics
all_values = tbl.column("value").to_numpy()
value_mean = all_values.mean()
value_std = all_values.std()

# Set color scale limits to mean ± 3 std
value_min = value_mean - 3 * value_std
value_max = value_mean + 3 * value_std

print(f"Global statistics: mean={value_mean:.4f}, std={value_std:.4f}")
print(f"Color scale range: {value_min:.4f} to {value_max:.4f}")
print(f"(Actual data range: {all_values.min():.4f} to {all_values.max():.4f})")

# Pre-compute layers
bin_layers = {}
for bin in unique_bins:
    layer_table = bin_tables[bin]

    # Get aggregated values
    values = layer_table.column("value").to_numpy()

    # Normalize using global min/max
    value_norm = (values - value_min) / (value_max - value_min)

    # Apply colormap to normalized aggregated values
    colors = apply_continuous_cmap(value_norm, Roma_10, alpha=1)

    # Create H3 layer
    layer = H3HexagonLayer(
        layer_table,
        get_hexagon=layer_table.column("h3_index"),
        get_fill_color=colors,
        filled=True,
        extruded=False,
        stroked=True,
        # the following option makes it work as expected, but much less performant with actual data set
        # high_precision=True,
    )

    # layer = ScatterplotLayer(
    #     layer_table,
    #     get_fill_color=colors,
    #     radius_min_pixels=1,
    #     radius_max_pixels=1,
    # )

    bin_layers[bin] = layer
    print(f"Pre-computed layer for {bin} ({len(layer_table)} hexagons)")

print("Pre-computation complete!")

In [ ]:
# Create the map with initial layer
current_minute_idx = 0
layer = bin_layers[unique_bins[current_minute_idx]]

map_widget = Map(
    layers=[layer],
    view_state={
        "latitude": 44.97,
        "longitude": -103.77,
        "zoom": 3,
        "pitch": 0,
        "bearing": 0,
    },
    height=600,
)

# Create a label to show current time
time_label = widgets.Label(value=f"Time: {unique_bins[0]}")

# Function to update the layer
def update_layer(bin_idx):
    bin = unique_bins[bin_idx]
    map_widget.layers = [bin_layers[bin]]
    time_label.value = f"Time: {bin} ({bin_idx + 1}/{len(unique_bins)})"

# Create widgets slider
slider = widgets.IntSlider(
    value=0,
    min=0,
    max=len(unique_bins) - 1,
    step=1,
    description="Frame:",
    continuous_update=True,
)

def on_slider_change(change):
    global current_minute_idx
    current_minute_idx = change["new"]
    update_layer(current_minute_idx)

slider.observe(on_slider_change, names="value")

# Display controls and map
controls = widgets.HBox([slider, time_label])
display(controls)
display(map_widget)